In [3]:
import os
import pandas as pd
import numpy as np
import datetime
from datetime import date

from dotenv import load_dotenv
from openai import AzureOpenAI
import tiktoken
from langchain_openai import AzureChatOpenAI

import csv
import time
from datetime import date, datetime

import re



os.getcwd()

'c:\\Users\\Denis_Davydov2\\OneDrive\\Scipts\\Py_Scripts\\EPAM\\Prophet\\AI_skills'

In [4]:

# Load filtered topics with embeddings
file_path = 'C:\\Users\\Denis_Davydov2\\OneDrive - EPAM\\Prophet_AI_docs\\Datasets\\AI_skills\\Topics\\'
file_name = 'ai_topics_final2025-11-10.csv'

topics = pd.read_csv(file_path+file_name)
print("File read: ", file_name)

topics

File read:  ai_topics_final2025-11-10.csv


id                     term  \
0         6.0          1-bit inference   
1         7.0                1-bit llm   
2         9.0       1-bit quantization   
3        14.0       2-bit quantization   
4        17.0             2d animation   
...       ...                      ...   
6966  19003.0  zero-shot voice cloning   
6967  19007.0      zero-trust security   
6968  19010.0              zero/zero++   
6969  19012.0                  zerogpu   
6970  19018.0              zmp control   

                                             definition  count  \
0     1-bit inference refers to the process of runni...    2.0   
1     A 1-bit large language model (LLM) is a highly...    5.0   
2     1-bit quantization is an extreme model compres...    6.0   
3     2-bit quantization is a process that reduces t...    4.0   
4     "2D animation" refers to the use of artificial...    3.0   
...                                                 ...    ...   
6966  Zero-shot voice cloning is the task of synthes...    3.0   
6967  Zero-trust security for AI/ML is an architectu...    4.0   
6968  "Zero" (zero-shot) refers to applying or evalu...    2.0   
6969  Zerogpu (often stylized "zerogpu") refers to C...    2.0   
6970  ZMP control (Zero Moment Point control) in AI/...    2.0   

      similarity_to_AI  consensus_score  \
0             0.280766                4   
1             0.220254                4   
2             0.187808                3   
3             0.190536                4   
4             0.370161                5   
...                ...              ...   
6966          0.212219                4   
6967          0.419530                5   
6968          0.243124                4   
6969          0.299549                4   
6970          0.289303                5   

                                         embedding_norm  
0     [0.013369597494602203, -0.013582168146967888, ...  
1     [0.017574984580278397, -0.004011554177850485, ...  
2     [-0.015226091258227825, 0.0012089560041204095,...  
3     [-0.006645898800343275, 0.006167215760797262, ...  
4     [0.008917991071939468, -0.002153154695406556, ...  
...                                                 ...  
6966  [-0.007965235970914364, -0.027662577107548714,...  
6967  [-0.01758248545229435, 0.059987302869558334, 0...  
6968  [-0.0007028839900158346, 0.011448170058429241,...  
6969  [0.004047493916004896, 0.05906970053911209, 0....  
6970  [0.04024605080485344, 0.04385624825954437, 0.0...  

[6971 rows x 7 columns]

In [5]:
topics1 = topics.copy()
topics1['full_text'] = topics1['term'] + '.\n' + topics1['definition']
topics1

id                     term  \
0         6.0          1-bit inference   
1         7.0                1-bit llm   
2         9.0       1-bit quantization   
3        14.0       2-bit quantization   
4        17.0             2d animation   
...       ...                      ...   
6966  19003.0  zero-shot voice cloning   
6967  19007.0      zero-trust security   
6968  19010.0              zero/zero++   
6969  19012.0                  zerogpu   
6970  19018.0              zmp control   

                                             definition  count  \
0     1-bit inference refers to the process of runni...    2.0   
1     A 1-bit large language model (LLM) is a highly...    5.0   
2     1-bit quantization is an extreme model compres...    6.0   
3     2-bit quantization is a process that reduces t...    4.0   
4     "2D animation" refers to the use of artificial...    3.0   
...                                                 ...    ...   
6966  Zero-shot voice cloning is the task of synthes...    3.0   
6967  Zero-trust security for AI/ML is an architectu...    4.0   
6968  "Zero" (zero-shot) refers to applying or evalu...    2.0   
6969  Zerogpu (often stylized "zerogpu") refers to C...    2.0   
6970  ZMP control (Zero Moment Point control) in AI/...    2.0   

      similarity_to_AI  consensus_score  \
0             0.280766                4   
1             0.220254                4   
2             0.187808                3   
3             0.190536                4   
4             0.370161                5   
...                ...              ...   
6966          0.212219                4   
6967          0.419530                5   
6968          0.243124                4   
6969          0.299549                4   
6970          0.289303                5   

                                         embedding_norm  \
0     [0.013369597494602203, -0.013582168146967888, ...   
1     [0.017574984580278397, -0.004011554177850485, ...   
2     [-0.015226091258227825, 0.0012089560041204095,...   
3     [-0.006645898800343275, 0.006167215760797262, ...   
4     [0.008917991071939468, -0.002153154695406556, ...   
...                                                 ...   
6966  [-0.007965235970914364, -0.027662577107548714,...   
6967  [-0.01758248545229435, 0.059987302869558334, 0...   
6968  [-0.0007028839900158346, 0.011448170058429241,...   
6969  [0.004047493916004896, 0.05906970053911209, 0....   
6970  [0.04024605080485344, 0.04385624825954437, 0.0...   

                                              full_text  
0     1-bit inference.\n1-bit inference refers to th...  
1     1-bit llm.\nA 1-bit large language model (LLM)...  
2     1-bit quantization.\n1-bit quantization is an ...  
3     2-bit quantization.\n2-bit quantization is a p...  
4     2d animation.\n"2D animation" refers to the us...  
...                                                 ...  
6966  zero-shot voice cloning.\nZero-shot voice clon...  
6967  zero-trust security.\nZero-trust security for ...  
6968  zero/zero++.\n"Zero" (zero-shot) refers to app...  
6969  zerogpu.\nZerogpu (often stylized "zerogpu") r...  
6970  zmp control.\nZMP control (Zero Moment Point c...  

[6971 rows x 8 columns]

In [6]:

# Add token count column
def num_tokens_from_string(string, encoding_name):
    encoding = tiktoken.get_encoding(encoding_name)
    num_tokens = len(encoding.encode(string if isinstance(string, str) else '', disallowed_special=()))
    return num_tokens

topics1['token_count'] = topics1['full_text'].apply(lambda text: num_tokens_from_string(text, "cl100k_base"))
topics1 = topics1[topics1['token_count']>0]

print("Total tokens:", topics1['token_count'].sum())
print("Min tokens:", topics1['token_count'].min())
print("Max tokens:", topics1['token_count'].max())
print("Total tokens:", topics1['token_count'].sum())
topics1

Total tokens: 478969
Min tokens: 27
Max tokens: 133
Total tokens: 478969


id                     term  \
0         6.0          1-bit inference   
1         7.0                1-bit llm   
2         9.0       1-bit quantization   
3        14.0       2-bit quantization   
4        17.0             2d animation   
...       ...                      ...   
6966  19003.0  zero-shot voice cloning   
6967  19007.0      zero-trust security   
6968  19010.0              zero/zero++   
6969  19012.0                  zerogpu   
6970  19018.0              zmp control   

                                             definition  count  \
0     1-bit inference refers to the process of runni...    2.0   
1     A 1-bit large language model (LLM) is a highly...    5.0   
2     1-bit quantization is an extreme model compres...    6.0   
3     2-bit quantization is a process that reduces t...    4.0   
4     "2D animation" refers to the use of artificial...    3.0   
...                                                 ...    ...   
6966  Zero-shot voice cloning is the task of synthes...    3.0   
6967  Zero-trust security for AI/ML is an architectu...    4.0   
6968  "Zero" (zero-shot) refers to applying or evalu...    2.0   
6969  Zerogpu (often stylized "zerogpu") refers to C...    2.0   
6970  ZMP control (Zero Moment Point control) in AI/...    2.0   

      similarity_to_AI  consensus_score  \
0             0.280766                4   
1             0.220254                4   
2             0.187808                3   
3             0.190536                4   
4             0.370161                5   
...                ...              ...   
6966          0.212219                4   
6967          0.419530                5   
6968          0.243124                4   
6969          0.299549                4   
6970          0.289303                5   

                                         embedding_norm  \
0     [0.013369597494602203, -0.013582168146967888, ...   
1     [0.017574984580278397, -0.004011554177850485, ...   
2     [-0.015226091258227825, 0.0012089560041204095,...   
3     [-0.006645898800343275, 0.006167215760797262, ...   
4     [0.008917991071939468, -0.002153154695406556, ...   
...                                                 ...   
6966  [-0.007965235970914364, -0.027662577107548714,...   
6967  [-0.01758248545229435, 0.059987302869558334, 0...   
6968  [-0.0007028839900158346, 0.011448170058429241,...   
6969  [0.004047493916004896, 0.05906970053911209, 0....   
6970  [0.04024605080485344, 0.04385624825954437, 0.0...   

                                              full_text  token_count  
0     1-bit inference.\n1-bit inference refers to th...           59  
1     1-bit llm.\nA 1-bit large language model (LLM)...           86  
2     1-bit quantization.\n1-bit quantization is an ...           63  
3     2-bit quantization.\n2-bit quantization is a p...           59  
4     2d animation.\n"2D animation" refers to the us...           63  
...                                                 ...          ...  
6966  zero-shot voice cloning.\nZero-shot voice clon...           72  
6967  zero-trust security.\nZero-trust security for ...           91  
6968  zero/zero++.\n"Zero" (zero-shot) refers to app...          102  
6969  zerogpu.\nZerogpu (often stylized "zerogpu") r...           76  
6970  zmp control.\nZMP control (Zero Moment Point c...           64  

[6971 rows x 9 columns]

In [7]:
unique_skills = ', '.join(topics1['term'].tolist())
print(f"Total skills: {len(topics1)}")
print(f"Total characters: {len(unique_skills)}")

Total skills: 6971
Total characters: 134359


In [21]:
# Refined prompt aligned with JSON grouping schema
# Builds the user message used alongside system_instructions.

# Note: system_instructions already enforce JSON structure. This prompt supplies raw skills and grouping guidance.

prompt = f"""You will be provided with a large set of AI-related skills used in development, deployment, governance, operations, productization, and applied data science.

Goal: Partition ALL provided AI skills into well-defined, non-overlapping categories for recruiting and talent development.

OUTPUT MUST BE ONLY JSON (enforced separately). DO NOT include explanations here.

Schema (each object):
  group_name  -> concise, specific category name (3-6 words, no internal quotes)
  department  -> functional area and a short definition in 1-2 sentences
  members     -> list of original skills belonging only to this category

Rules:
- Use every original skill exactly once (coverage = 100%, no duplicates across groups).
- Preserve each skill string verbatim (do not correct, merge, or split).
- Target about 100 groups; if impossible, still cover all skills.
- Each group should contain >=2 skills; if a skill would stand alone, merge it with the closest related group.
- Avoid generic names ("General", "Misc", "Other") unless used for a final residual set of <10 uncategorizable items.
- Prefer domain + action or domain + focus patterns (e.g., "Model Performance Evaluation", "LLM Prompt Engineering", "Data Quality Assurance", "AI Risk & Compliance").
- If two candidate groups would be extremely small (<2 skills each), combine them.

Strategy Hints (do not output):
- Cluster by shared technology (e.g., PyTorch/TensorFlow), lifecycle phase (development, deployment, monitoring), modality (vision, text, audio), and governance aspects.
- Keep prompt engineering separate from model fine-tuning where possible.
- Separate infra (scaling, orchestration) from modeling (training, optimization) and from governance (risk, ethics).

Initial large skill set:
{unique_skills}
"""

print(prompt)

You will be provided with a large set of AI-related skills used in development, deployment, governance, operations, productization, and applied data science.

Goal: Partition ALL provided AI skills into well-defined, non-overlapping categories for recruiting and talent development.

OUTPUT MUST BE ONLY JSON (enforced separately). DO NOT include explanations here.

Schema (each object):
  group_name  -> concise, specific category name (3-6 words, no internal quotes)
  department  -> functional area and a short definition in 1-2 sentences
  members     -> list of original skills belonging only to this category

Rules:
- Use every original skill exactly once (coverage = 100%, no duplicates across groups).
- Preserve each skill string verbatim (do not correct, merge, or split).
- Target about 100 groups; if impossible, still cover all skills.
- Each group should contain >=2 skills; if a skill would stand alone, merge it with the closest related group.
- Avoid generic names ("General", "Mis

In [22]:
# === Load Environment Variables ===
load_dotenv()  # Loads variables from .env file into environment

# Retrieve database connection parameters from environment variables
DIAL_API_KEY = os.getenv('DIAL_API_KEY')

#print(DIAL_API_KEY)

In [23]:
# LangChain with system message -> structured JSON output
import json
from typing import List, Dict

# Initialize the Azure OpenAI model
model = AzureChatOpenAI(
    azure_endpoint="https://ai-proxy.lab.epam.com",
    api_key=DIAL_API_KEY,
    api_version="2025-04-01-preview",
    model='gpt-5-2025-08-07'
)

# Refined system directive: strict JSON, target schema, semantic grouping guidance
system_instructions = (
    "You are an expert in talent acquisition and employee training for AI development and implementation teams. "
    "Task: Group the provided AI-related skill list into generalized categories that are useful for recruiting and workforce development. "
    "Return ONLY a valid JSON array (UTF-8) with objects of this exact schema: \n"
    "[\n  {\n    \"group_name\": \"string\",       // short, specific, human-readable category name (3-6 words, no quotes inside)\n    \"department\": \"string\",       // functional area (A short definition in 1-2 sentences)\n    \"members\": [\"skill1\", \"skill2\", ...]  // original skills belonging to this group (>=2)\n  }\n] \n"
    "Requirements: \n"
    "- Minimum 100 groups if possible; otherwise cover all skills. \n"
    "- Every original skill must appear in exactly one group's members (no omissions, no duplicates across groups). \n"
    "- Preserve original skill text verbatim (case, punctuation). \n"
    "- Do NOT include definitions or summaries; only the three specified keys. \n"
    "- Use only double quotes for JSON; no trailing commas. \n"
    "- Avoid overly broad names like 'General' or 'Misc'; prefer precise domain-centric labels. \n"
    "- Exclude commentary, explanations, markdown, or code fences. Output MUST start with '[' and end with ']'. \n"
    "If perfect one-to-one grouping is impossible, still ensure no skill is lost."
)

# Build messages for chat model
messages = [
    ("system", system_instructions),
    ("human", prompt),
]

ts_start = datetime.now()
print('Start:', ts_start)

# Invoke model
output = model.invoke(messages)
raw_response = output.content.strip()

# Attempt to locate JSON block (robust stripping of leading/trailing text)
def extract_json(text: str) -> str:
    if text.startswith('```'):
        parts = text.split('```')
        if len(parts) >= 2:
            text = parts[1]
    start = text.find('[')
    end = text.rfind(']')
    if start != -1 and end != -1 and end > start:
        return text[start:end+1]
    raise ValueError('JSON array delimiters not found in model output.')

try:
    json_str = extract_json(raw_response)
    data = json.loads(json_str)
except Exception as e:
    print('Failed to parse JSON automatically:', e)
    cleaned = raw_response.replace('\n', ' ').replace('\r', ' ').strip('`')
    try:
        json_str = extract_json(cleaned)
        data = json.loads(json_str)
    except Exception as e2:
        print('Secondary parse failed:', e2)
        data = []

# Basic validation & repair (enforce required keys, uniqueness, coverage)
all_skills = set(topics1['term'].tolist())
covered = set()
valid_rows = []
for obj in data:
    if not isinstance(obj, dict):
        continue
    group_name = obj.get('group_name')
    department = obj.get('department') or 'General'
    members = obj.get('members')
    if not (group_name and isinstance(department, str) and isinstance(members, list)):
        continue
    members_clean = [m for m in members if isinstance(m, str) and m.strip()]
    # Deduplicate members within group while preserving order
    seen_local = set()
    members_dedup = []
    for m in members_clean:
        if m not in seen_local:
            seen_local.add(m)
            members_dedup.append(m)
    # Filter to skills that exist in original set
    members_filtered = [m for m in members_dedup if m in all_skills]
    if len(members_filtered) < 2:
        continue
    valid_rows.append({'group_name': group_name, 'department': department, 'members': members_filtered})
    covered.update(members_filtered)

missing = all_skills - covered
if missing:
    print(f"Warning: {len(missing)} skills not covered; adding fallback group.")
    valid_rows.append({
        'group_name': 'Residual Specialized Skills',
        'department': 'Other',
        'members': sorted(missing)
    })

# Ensure no skill appears twice (if duplicates occurred, keep first occurrence only)
seen_global = set()
for row in valid_rows:
    unique_members = []
    for m in row['members']:
        if m not in seen_global:
            seen_global.add(m)
            unique_members.append(m)
    row['members'] = unique_members

import pandas as pd
required_cols = ['group_name', 'department', 'members']
df_groups = pd.DataFrame(valid_rows, columns=required_cols)

# Summary stats
print(f"Parsed groups: {len(df_groups)}; total skills covered: {sum(len(x) for x in df_groups['members'])}; unique skills: {len(seen_global)}")

ts_end = datetime.now()
print('LLM Finish:', ts_end)
print('Processing time:', ts_end - ts_start)

df_groups

Start: 2025-11-10 22:34:58.693396
Parsed groups: 171; total skills covered: 6971; unique skills: 6971
LLM Finish: 2025-11-10 22:38:34.732791
Processing time: 0:03:36.039395
Parsed groups: 171; total skills covered: 6971; unique skills: 6971
LLM Finish: 2025-11-10 22:38:34.732791
Processing time: 0:03:36.039395


group_name  \
0             Quantization and Low Precision   
1    Inference Optimization and Acceleration   
2       Distributed Training and Parallelism   
3      Transformers and Attention Mechanisms   
4          Model Evaluation and Benchmarking   
..                                       ...   
166                 Speech Synthesis and TTS   
167               Vector Indexing and Stores   
168           Document Processing and Layout   
169             Security Operations and SIEM   
170              Residual Specialized Skills   

                                            department  \
0    Model Optimization focuses on reducing model s...   
1    Model Serving and Performance focuses on optim...   
2    AI Infrastructure Engineering designs scalable...   
3    Model Development focuses on transformer archi...   
4    Model Governance defines evaluation protocols,...   
..                                                 ...   
166  Audio AI develops TTS voices and speech synthe...   
167  Data Platform provisions indexing for fast vec...   
168  Document AI extracts structure and content fro...   
169  Security Engineering monitors and responds to ...   
170                                              Other   

                                               members  
0    [1-bit quantization, 2-bit quantization, 4-bit...  
1    [1-bit inference, 8-bit training, batch infere...  
2    [distributed training, distributed ai training...  
3    [transformer, transformer architecture, transf...  
4    [evaluation & benchmarking, evaluation (evals)...  
..                                                 ...  
166  [text-to-speech (tts), ssml and text-to-speech...  
167                                                 []  
168                                                 []  
169                                 [siem, cloud siem]  
170  [1-bit llm, 2d animation, 2d-to-3d conversion,...  

[171 rows x 3 columns]

In [19]:
skills2 = df_groups
skills2

group_name  \
0               LLM Prompt Engineering   
1              Prompt Security Defense   
2              LLM Fine Tuning Methods   
3                LLM Inference Serving   
4                 LLM Safety Alignment   
..                                 ...   
107  Scheduling Parallel Orchestration   
108          Caching Memory Efficiency   
109            Long Context Management   
110            Image Editing Upscaling   
111        Residual Specialized Skills   

                                            department  \
0    Model behavior design for generative AI. Focus...   
1    Application security for LLM-driven systems. P...   
2    Model adaptation and efficiency techniques. Sp...   
3    Productionization of LLMs. Focuses on scalable...   
4    Risk mitigation and alignment for LLM systems....   
..                                                 ...   
107  Resource and pipeline scheduling. Scales distr...   
108  Caching strategies for inference. Reduces late...   
109  Scaling context windows. Optimizes processing ...   
110  Image-to-image and enhancement. Applies inpain...   
111                                              Other   

                                               members  
0    [prompt engineering, prompt design, prompt opt...  
1    [prompt injection, prompt injection detection,...  
2    [fine-tuning (llm), llm finetuning, supervised...  
3    [llm inference, llm serving, llm streaming, ll...  
4    [llm safety, llm guardrails, alignment, ai ali...  
..                                                 ...  
107  [workload scheduling, resource scheduling, sch...  
108  [caching, cache optimization, kv cache managem...  
109  [long context window, long context handling, l...  
110  [image-to-image generation, image editing, ima...  
111  [1-bit inference, 1-bit llm, 1-bit quantizatio...  

[112 rows x 3 columns]